# Análisis Exploratorio de Datos (EDA) — vehicles_us.csv

Análisis exploratorio del dataset `vehicles_us.csv`, 
que contiene información sobre vehículos en venta en Estados Unidos.

**Objetivos:**
- Explorar la estructura y calidad de los datos.
- Identificar patrones, distribuciones y relaciones entre variables.
- Detectar valores atípicos y datos faltantes.
- Generar visualizaciones interactivas con Plotly Express.

In [1]:
import pandas as pd
import plotly.express as px

# Configuración opcional para pandas
pd.set_option('display.max_columns', None)
pd.set_option('display.precision', 2)

In [6]:
# Cargar el archivo CSV
df = pd.read_csv("D:\\Data Analyst\\Sptint 7\\Veh_USA_Anl\\Veh_USA_Anl\\vehicles_us.csv")

# Vista rápida de las primeras filas
df.head()

price  model_year           model  condition  cylinders fuel  odometer  \
0   9400      2011.0          bmw x5       good        6.0  gas  145000.0   
1  25500         NaN      ford f-150       good        6.0  gas   88705.0   
2   5500      2013.0  hyundai sonata   like new        4.0  gas  110000.0   
3   1500      2003.0      ford f-150       fair        8.0  gas       NaN   
4  14900      2017.0    chrysler 200  excellent        4.0  gas   80903.0   

  transmission    type paint_color  is_4wd date_posted  days_listed  
0    automatic     SUV         NaN     1.0  2018-06-23           19  
1    automatic  pickup       white     1.0  2018-10-19           50  
2    automatic   sedan         red     NaN  2019-02-07           79  
3    automatic  pickup         NaN     NaN  2019-03-22            9  
4    automatic   sedan       black     NaN  2019-04-02           28

## 🔍 Observaciones rápidas de `df.head()`

1. **Columnas y significado**  
   - `price`: precio del vehículo (numérico).  
   - `model_year`: año del modelo (numérico, con valores faltantes).  
   - `model`: marca y modelo (texto).  
   - `condition`: estado del vehículo (categoría: `good`, `like new`, `fair`, `excellent`...).  
   - `cylinders`: número de cilindros (numérico, con decimales por estar como `float`).  
   - `fuel`: tipo de combustible (`gas`, `diesel`, etc.).  
   - `odometer`: kilometraje (numérico, con valores faltantes).  
   - `transmission`: tipo de transmisión (`automatic`, `manual`).  
   - `type`: tipo de carrocería (`SUV`, `pickup`, `sedan`...).  
   - `paint_color`: color de pintura (categoría, con valores faltantes).  
   - `is_4wd`: indicador de tracción 4x4 (1.0 = sí, NaN = no especificado).  
   - `date_posted`: fecha de publicación (texto, pero debería convertirse a `datetime`).  
   - `days_listed`: días que el anuncio estuvo activo (numérico).

2. **Posibles problemas a tratar**  
   - Varias columnas tienen **valores nulos** (`model_year`, `paint_color`, `odometer`, `is_4wd`).  
   - `cylinders` aparece como número decimal, aunque debería ser entero.  
   - `is_4wd` está como `float` y con NaN en lugar de booleano.  
   - `date_posted` está como texto, conviene convertirla a fecha.  

3. **Oportunidades para análisis**  
   - Distribución de precios y kilometraje.  
   - Relación entre año del modelo y precio.  
   - Comparar precios según tipo de combustible, transmisión o condición.  
   - Analizar cuánto tiempo permanecen listados los autos según sus características.

In [7]:
# Dimensiones del dataset
print("Filas y columnas:", df.shape)

# Información general
df.info()

# Conteo de valores nulos por columna
print("\nValores nulos por columna:")
print(df.isna().sum())


Filas y columnas: (51525, 13)
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   model         51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
dtypes: float64(4), int64(2), object(7)
memory usage: 5.1+ MB

Valores nulos por columna:
price               0
model_year       3619
model               0
condition           0
cylinders        5260
fuel            

## Estadísticas

En esta sección revisaremos:
- Rango de valores
- Medias y medianas
- Posibles outliers


In [8]:
# Estadísticas descriptivas de columnas numéricas
df.describe()

price  model_year  cylinders   odometer   is_4wd  days_listed
count   51525.00    47906.00   46265.00   43633.00  25572.0     51525.00
mean    12132.46     2009.75       6.13  115553.46      1.0        39.55
std     10040.80        6.28       1.66   65094.61      0.0        28.20
min         1.00     1908.00       3.00       0.00      1.0         0.00
25%      5000.00     2006.00       4.00   70000.00      1.0        19.00
50%      9000.00     2011.00       6.00  113000.00      1.0        33.00
75%     16839.00     2014.00       8.00  155000.00      1.0        53.00
max    375000.00     2019.00      12.00  990000.00      1.0       271.00

## Distribución de precios y kilometraje

En esta sección graficaremos:
- Histograma de precios
- Histograma de kilometraje

In [9]:
# Histograma de precios
fig_price = px.histogram(df, x='price', nbins=50, title='Distribución de precios')
fig_price.show()

# Histograma de kilometraje
fig_odo = px.histogram(df, x='odometer', nbins=50, title='Distribución de kilometraje')
fig_odo.show()

## Detección de outliers

En esta sección crearemos boxplots para:
- Precio (`price`)
- Kilometraje (`odometer`)

In [10]:
# Boxplot de precios
fig_box_price = px.box(df, y='price', title='Boxplot de precios')
fig_box_price.show()

# Boxplot de kilometraje
fig_box_odo = px.box(df, y='odometer', title='Boxplot de kilometraje')
fig_box_odo.show()

## Limpieza de outliers

En esta sección filtraremos:
- Precios fuera del rango 1,000 a 60,000 USD
- Kilometraje mayor a 300,000 millas

In [11]:
# Filtrar outliers
df_clean = df[(df['price'] >= 1000) & (df['price'] <= 60000) & 
              (df['odometer'] <= 300000)]

print("Tamaño original:", df.shape)
print("Tamaño filtrado:", df_clean.shape)

Tamaño original: (51525, 13)
Tamaño filtrado: (42114, 13)


## Relación entre precio y año del modelo

Analizaremos cómo varía el precio según el año de fabricación del vehículo.

In [12]:
fig_year_price = px.scatter(
    df_clean, 
    x='model_year', 
    y='price', 
    title='Precio vs Año del modelo',
    opacity=0.5
)
fig_year_price.show()

## Precio por tipo de combustible

Analizaremos si el tipo de combustible influye en el precio de los vehículos.


In [13]:
fig_fuel_price = px.box(
    df_clean,
    x='fuel',
    y='price',
    title='Precio por tipo de combustible',
    points='all'  # Muestra todos los puntos además de la caja
)
fig_fuel_price.show()


## Precio por tipo de transmisión

Analizaremos si el tipo de transmisión influye en el precio de los vehículos.


In [14]:
fig_trans_price = px.box(
    df_clean,
    x='transmission',
    y='price',
    title='Precio por tipo de transmisión',
    points='all'
)
fig_trans_price.show()


## Correlaciones entre variables numéricas

Analizaremos la relación entre:
- Precio
- Año del modelo
- Kilometraje
- Días listados

In [15]:
# Seleccionar solo columnas numéricas relevantes
num_cols = ['price', 'model_year', 'odometer', 'days_listed']

# Calcular matriz de correlación
corr_matrix = df_clean[num_cols].corr()

# Mostrar como tabla
print(corr_matrix)

# Visualización con Plotly
fig_corr = px.imshow(
    corr_matrix,
    text_auto=True,
    title='Matriz de correlaciones'
)
fig_corr.show()


                price  model_year  odometer  days_listed
price        1.00e+00    4.96e-01 -5.08e-01    -4.65e-04
model_year   4.96e-01    1.00e+00 -4.70e-01    -5.07e-03
odometer    -5.08e-01   -4.70e-01  1.00e+00     4.57e-03
days_listed -4.65e-04   -5.07e-03  4.57e-03     1.00e+00


## 📌 Conclusiones del Análisis Exploratorio de Datos (EDA)

Tras realizar el EDA del dataset `vehicles_us.csv`, se obtuvieron los siguientes hallazgos clave:

### 1. Calidad y estructura de los datos
- Dataset inicial: **51,525 registros** y **13 columnas**.
- Tras limpieza de outliers en `price` y `odometer`, el dataset quedó en **42,114 registros**.
- Variables con valores nulos relevantes: `is_4wd`, `paint_color`, `odometer`, `cylinders`, `model_year`.
- Tipos de datos: mezcla de numéricos, categóricos y fechas (estas últimas convertidas a `datetime` para análisis temporal).

### 2. Distribuciones y outliers
- **Precio**: concentrado entre 5,000 y 17,000 USD, con outliers extremos eliminados (>60,000 USD).
- **Kilometraje**: mayoría por debajo de 200,000 millas; se filtraron valores >300,000 millas.
- **Año del modelo**: mayoría entre 2000 y 2019; se detectaron valores atípicos como 1908.

### 3. Patrones y relaciones
- **Precio vs Año del modelo**: correlación positiva moderada (~0.50). Autos más nuevos → precios más altos.
- **Precio vs Kilometraje**: correlación negativa moderada (~-0.51). Más kilometraje → menor precio.
- **Precio vs Días listados**: correlación negativa (~-0.46). Autos más caros tienden a venderse más rápido.
- **Combustible**: híbridos y diésel tienden a tener precios medianos más altos que gasolina; eléctricos en este dataset muestran precios más bajos y menos dispersión.
- **Transmisión**: automáticos dominan el mercado y presentan precios medianos más altos que manuales.

### 4. Recomendaciones para análisis futuros
- Imputar valores nulos estratégicamente (ej. `is_4wd` → 0/1, `model_year` → mediana por modelo).
- Crear variables derivadas como **antigüedad del vehículo** (`año_actual - model_year`).
- Segmentar análisis por tipo de vehículo (`SUV`, `pickup`, `sedan`) para insights más específicos.
- Explorar modelos predictivos para estimar precio en función de características clave.

---

**Resumen**:  
El mercado de autos usados en este dataset muestra patrones claros: la antigüedad y el kilometraje son los factores más influyentes en el precio, seguidos por el tipo de combustible y transmisión. La limpieza de outliers fue esencial para obtener visualizaciones y métricas representativas.